Neural Networks

In [1]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import ast
import numpy as np

from sklearn.neural_network import MLPRegressor

In [0]:
df_test=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/01_Data/02_Clean/test.csv')
df_train=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/01_Data/02_Clean/train.csv')

inputs=['ambient', 'coolant', 'u_d', 'u_q', 'speed', 'i_d', 'i_q']    #identify the input features
outputs=['pm','yoke', 'tooth', 'winding']              #identify the output features

#split into X and y data
X_test=df_test[inputs].reset_index(drop=True) 
y_test=df_test[outputs].reset_index(drop=True) 

X_train=df_train[inputs].reset_index(drop=True) 
y_train=df_train[outputs].reset_index(drop=True)

In [0]:
def MSE(predic,ref):
  diff=(predic-ref)**2
  mean_diff=diff.mean()
  return mean_diff

In [0]:
scores=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/02_testing_parameters_MLP.csv',sep='/', converters={"Layers": ast.literal_eval})
scores['model_score']=0
scores['iteration']=0
scores['MSE_pm']=0
scores['MSE_yoke']=0
scores['MSE_tooth']=0
scores['MSE_winding']=0

In [0]:
scores.head()

Layers activation solver  ...  MSE_yoke  MSE_tooth MSE_winding
0  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...         0          0           0
1  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...         0          0           0
2  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...         0          0           0
3  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...         0          0           0
4  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...         0          0           0

[5 rows x 12 columns]

a loop to perform experiments by changing the value of hyperparameters

In [0]:
for i in scores.index:
  model=MLPRegressor(hidden_layer_sizes=scores['Layers'][i],activation=scores['activation'][i],solver=scores['solver'][i],batch_size=scores['batch'][i],learning_rate_init=scores['learning'][i],learning_rate=scores['learning_type'][i])
  model.fit(X_train,y_train)
  y_pred=model.predict(X_test)
  y_pred=pd.DataFrame(y_pred,columns=y_test.columns)

  scores.loc[i,'model_score']=model.score(X_test,y_test)
  scores.loc[i,'MSE_pm']=MSE(y_pred,y_test)['pm']
  scores.loc[i,'MSE_yoke']=MSE(y_pred,y_test)['yoke']
  scores.loc[i,'MSE_tooth']=MSE(y_pred,y_test)['tooth']
  scores.loc[i,'MSE_winding']=MSE(y_pred,y_test)['winding']
  scores.loc[i,'iteration']=model.n_iter_

  print(i)


In [0]:
scores.to_csv(path_or_buf='/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/scores_NN.csv')

Displaying graph to understand the weight of each hyperparameter

In [0]:
scores_NN=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/scores_NN.csv',sep='/')

In [0]:
scores_NN.head()

Layers activation solver  ...  MSE_yoke  MSE_tooth MSE_winding
0  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...  0.087105   0.150245    0.171978
1  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...  0.073371   0.138006    0.171369
2  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...  0.120534   0.192451    0.214863
3  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...  0.062175   0.112921    0.147196
4  (7, 7, 7, 6, 5, 4)       tanh    sgd  ...  0.063490   0.124736    0.158821

[5 rows x 12 columns]

In [0]:
group_achritecture=scores_NN.groupby(by='Layers').mean()
group_activation=scores_NN.groupby(by='activation').mean()
group_solver=scores_NN.groupby(by='solver').mean()
group_batch=scores_NN.groupby(by='batch').mean()
group_learning_rate=scores_NN.groupby(by='learning').mean()
group_learning_type=scores_NN.groupby(by='learning_type').mean()

In [0]:
fig = make_subplots(rows=3, cols=2,subplot_titles=("Solver", "Batch", "Activation","learning_rate", "Achritecture","learning_type"))

# Add traces
fig.add_trace(go.Scatter(x=group_solver.index, y=group_solver.model_score,mode='lines+markers',name='solver'), row=1, col=1)
fig.add_trace(go.Scatter(x=group_activation.index, y=group_activation.model_score,mode='lines+markers',name='activation'), row=2, col=1)
fig.add_trace(go.Scatter(x=group_achritecture.index, y=group_achritecture.model_score,mode='lines+markers',name='achritecture'), row=3, col=1)
fig.add_trace(go.Scatter(x=group_batch.index, y=group_batch.model_score,mode='lines+markers',name='batch'), row=1, col=2)
fig.add_trace(go.Scatter(x=group_learning_rate.index, y=group_learning_rate.model_score,mode='lines+markers',name='learning_rate'), row=2, col=2)
fig.add_trace(go.Scatter(x=group_learning_type.index, y=group_learning_type.model_score,mode='lines+markers',name='learning_type'), row=3, col=2)


fig['layout'].update(title='Impact of hyperparameters of the model score',showlegend=False)
fig['layout']['yaxis1'].update(range=[0.6, 1], autorange=False)
fig['layout']['yaxis2'].update(range=[0.6, 1], autorange=False)
fig['layout']['yaxis3'].update(range=[0.6, 1], autorange=False)
fig['layout']['yaxis4'].update(range=[0.6, 1], autorange=False)
fig['layout']['yaxis5'].update(range=[0.6, 1], autorange=False)
fig['layout']['yaxis6'].update(range=[0.6, 1], autorange=False)
fig.show()

A last test with the best combination of the parameters

In [0]:
model=MLPRegressor(hidden_layer_sizes=(20,10,20),activation='tanh',solver='adam',batch_size=700,learning_rate_init=0.003,learning_rate='adaptive')
model.fit(X_train,y_train)
y_pred=model.predict(X_test)
y_pred=pd.DataFrame(y_pred,columns=y_test.columns)

In [0]:
MSE(y_pred,y_test)

pm         0.241059
yoke       0.075924
tooth      0.130145
winding    0.164964
dtype: float64

In [0]:
model.score(X_test,y_test)

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



0.8611485366510122

In [0]:
fig_pred = make_subplots(rows=2, cols=1,vertical_spacing = 0.02,row_heights=[0.3, 0.7])
fig_pred.add_trace(go.Scatter(y=y_pred.pm,mode='lines',line={'color':'teal'},name="prediction"),row=2, col=1)
fig_pred.add_trace(go.Scatter(y=y_test.pm,mode='lines',line={'color':'black'},name="real values"),row=2, col=1)
fig_pred.add_trace(go.Scatter(y=((y_pred.pm-y_test.pm)**2),mode='lines',line={'color':'grey'},name="squared error"),row=1, col=1)

fig_pred['layout']['yaxis1'].update(range=[0, 2], autorange=False)
fig_pred['layout']['xaxis1'].update(visible=False)
fig_pred.show()

In [0]:
y_pred.to_csv(path_or_buf='/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/y_pred_NN.csv')

Validation:
In this part, we will switch the training and testing datasets in order to check whether the model has the same score or not

In [0]:
df_raw=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/01_Data/01_Raw/pmsm_temperature_data.csv')
df_raw=df_raw.drop(['torque'],axis=1)
#we rename the columns
df_raw.columns=['ambient', 'coolant', 'u_d', 'u_q', 'speed', 'i_d', 'i_q', 'pm','yoke', 'tooth', 'winding', 'profile_id']
batches=df_raw.profile_id.unique()
np.random.shuffle(batches)
scores=pd.DataFrame()

In [0]:
def MSE(predic,ref):
  diff=(predic-ref)**2
  mean_diff=diff.mean()
  return mean_diff

In [0]:
i=0
for i in range (0,batches.size-1,2):
  df_test=df_raw[(df_raw.profile_id==batches[i])|(df_raw.profile_id==batches[i+1])]
  df_train=df_raw[(df_raw.profile_id!=batches[i])&(df_raw.profile_id!=batches[i+1])]

  inputs=['ambient', 'coolant', 'u_d', 'u_q', 'speed', 'i_d', 'i_q']    #identify the input features
  outputs=['pm','yoke', 'tooth', 'winding']              #identify the output features

  #split into X and y data
  X_test=df_test[inputs].reset_index(drop=True) 
  y_test=df_test[outputs].reset_index(drop=True) 

  X_train=df_train[inputs].reset_index(drop=True) 
  y_train=df_train[outputs].reset_index(drop=True)

  model=MLPRegressor(hidden_layer_sizes=(20,10,20),activation='tanh',solver='adam',batch_size=700,learning_rate_init=0.003,learning_rate='adaptive')
  model.fit(X_train,y_train)
  y_pred=model.predict(X_test)
  y_pred=pd.DataFrame(y_pred,columns=y_test.columns)
  MSE(y_pred,y_test)
  model.score(X_test,y_test)

  scores.loc[i,'test_1']=batches[i]
  scores.loc[i,'test_2']=batches[i+1]
  scores.loc[i,'model_score']=model.score(X_test,y_test)
  scores.loc[i,'MSE_pm']=MSE(y_pred,y_test)['pm']
  scores.loc[i,'MSE_yoke']=MSE(y_pred,y_test)['yoke']
  scores.loc[i,'MSE_tooth']=MSE(y_pred,y_test)['tooth']
  scores.loc[i,'MSE_winding']=MSE(y_pred,y_test)['winding']
  print(i)

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



0


/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



2


/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



...

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



46


/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



48
50


/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').

/usr/local/lib/python3.6/dist-packages/sklearn/base.py:434: FutureWarning:

The default value of multioutput (not exposed in score method) will change from 'variance_weighted' to 'uniform_average' in 0.23 to keep consistent with 'metrics.r2_score'. To specify the default value manually and avoid the warning, please either call 'metrics.r2_score' directly or make a custom scorer with 'metrics.make_scorer' (the built-in scorer 'r2' uses multioutput='uniform_average').



In [0]:
scores.to_csv(path_or_buf='/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/NN_validation.csv')

In [0]:
validation_score=pd.read_csv('/content/gdrive/My Drive/Data Science/Electric_motor_temperature/03_Ressources/NN_validation.csv')
validation_score['test_1'] = validation_score['test_1'].astype(int)
validation_score['test_2'] = validation_score['test_2'].astype(int)
validation_score=validation_score.drop(['Unnamed: 0'],axis=1)
validation_score['test_batch']=validation_score[['test_1', 'test_2']].apply(tuple, axis=1)
validation_score['test_batch'] = validation_score['test_batch'].astype(str)

In [44]:
validation_score

test_1  test_2  model_score  ...  MSE_tooth  MSE_winding  test_batch
0       55      10     0.844151  ...   0.161115     0.231317    (55, 10)
1       79      36     0.661819  ...   0.445216     0.604628    (79, 36)
2       66      43     0.562966  ...   0.284214     0.294564    (66, 43)
3       11      69     0.724998  ...   0.221539     0.302722    (11, 69)
4       56      42     0.861231  ...   0.108538     0.164921    (56, 42)
5       45      54     0.793498  ...   0.118349     0.168862    (45, 54)
6        4      30     0.493606  ...   0.223618     0.283498     (4, 30)
7       52      20     0.825023  ...   0.169767     0.214987    (52, 20)
8       68      70     0.645471  ...   0.252119     0.303127    (68, 70)
9       50      49     0.681941  ...   0.158898     0.227126    (50, 49)
10      59      61     0.797966  ...   0.138891     0.187856    (59, 61)
11      81      31     0.751434  ...   0.130496     0.160343    (81, 31)
12      60      58     0.856529  ...   0.104916     0.162811    (60, 58)
13      75      74     0.622684  ...   0.251524     0.294499    (75, 74)
14      44      29     0.578187  ...   0.349149     0.485211    (44, 29)
15      80      63     0.539467  ...   0.202658     0.270646    (80, 63)
16      73      77     0.712863  ...   0.161469     0.200891    (73, 77)
17      57      76     0.753628  ...   0.201253     0.246471    (57, 76)
18      46      62     0.673973  ...   0.272184     0.351294    (46, 62)
19      47      65     0.771772  ...   0.165803     0.224648    (47, 65)
20      27      51     0.831255  ...   0.202963     0.276744    (27, 51)
21      67      53     0.772005  ...   0.109197     0.149672    (67, 53)
22      64      72     0.595582  ...   0.242905     0.303693    (64, 72)
23      78      71     0.550390  ...   0.202725     0.247655    (78, 71)
24      32       6     0.794150  ...   0.189125     0.258735     (32, 6)
25      41      48     0.461928  ...   0.230878     0.272634    (41, 48)

[26 rows x 8 columns]

In [55]:
fig = go.Figure()
# Add traces
fig.add_trace(go.Scatter(x=validation_score.test_batch, y=validation_score.model_score,mode='lines+markers',name='model score'))
fig.add_trace(go.Scatter(x=validation_score.test_batch, y=validation_score.MSE_pm,mode='lines+markers',name='MSE pm'))
fig.add_trace(go.Scatter(x=validation_score.test_batch, y=validation_score.MSE_yoke,mode='lines+markers',name='MSE yoke'))
fig.add_trace(go.Scatter(x=validation_score.test_batch, y=validation_score.MSE_tooth,mode='lines+markers',name='MSE tooth'))
fig.add_trace(go.Scatter(x=validation_score.test_batch, y=validation_score.MSE_winding,mode='lines+markers',name='MSE winging'))
fig.update_layout(title_text='Model quality with diffrent training datasets',legend_orientation="h",legend=dict(x=-.1, y=1.1))
fig['layout'].update(xaxis_title="Test data set")
fig.show()
